# gpCAM Test Notebook
In this notebook we will go through many features of gpCAM. Work through it 
and you are ready for your own autonomous experiment. This notebook uses gpCAM version 8 which is coming soon!

In [1]:
####install gpcam here if you do not have already done so
#!pip install gpcam==8.0.0

## This first cell has nothing to do with gpCAM, it's just a function to plot some results later

In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
import plotly.graph_objects as go
import numpy as np
def plot(x,y,z,data = None):
    fig = go.Figure()
    fig.add_trace(go.Surface(x = x, y = y,z=z))
    if data is not None: 
        fig.add_trace(go.Scatter3d(x=data[:,0], y=data[:,1], z=data[:,2],
                                   mode='markers'))

    fig.update_layout(title='Posterior Mean', autosize=True,
                  width=800, height=800,
                  margin=dict(l=65, r=50, b=65, t=90))


    fig.show()

## Here we want to define some points at which we will predict, still has nothing to do with gpCAM 

In [4]:
x_pred = np.zeros((10000,2))
x = np.linspace(0,10,100)
y = np.linspace(0,10,100)
x,y = np.meshgrid(x,y)
counter = 0
for i in  range(100):
    for j in range(100):
        x_pred[counter] = np.array([x[i,j],y[i,j]])
        counter += 1

## Let's get after it by setting up a Single-Task GP Autonomous Data Acquisition Run
### The following function are optional and already show you some advanced features

In [5]:
def optional_acq_func(x,obj):
    #this acquisition function makes the autonomous experiment a Bayesian optimization
    #but is just here as an example. 'acq_funciton="ucb"' will give you the same result
    a = 3.0 #3.0 for 95 percent confidence interval
    mean = obj.posterior_mean(x)["f(x)"]
    cov = obj.posterior_covariance(x)["v(x)"]
    return mean + a * np.sqrt(cov)

def optional_mean_func(x,hyperparameters,gp_obj):
    #the prior mean function should return a vector: a mean function evaluation for every x
    return np.zeros((len(x)))

def optional_cost_function(origin,x,arguments = None):
    #cost pf l1 motion in the input space
    offset = arguments["offset"]
    slope = arguments["slope"]
    d = np.abs(np.subtract(origin,x))
    c = (d * slope) + offset
    n = np.sum(c)
    return n

def optional_cost_update_function(costs, parameters):
    ###defining a cost update function might look tricky but just needs a bit
    ###of tenacity. And remember, this is optional, if you have a great guess for your costs you
    ###don't need to update the costs. Also, if you don't account for costs, this function is not needed.
    #In this example we just return the old parameters, but print the costs. 
    #I hope it is clear how the parameters can be fitted to the recorded costs.
    print("recorded costs (from,to,costs): ", costs)
    
    return parameters

In [6]:
import time
from gpcam import AutonomousExperimenterGP

def instrument(data):
    print("Suggested by gpCAM: ")
    for entry in data:
        print("suggested:", entry["x_data"])
        entry["y_data"] = np.sin(np.linalg.norm(entry["x_data"]))
        entry["cost"]  = [np.array([0,0]),entry["x_data"],np.sum(entry["x_data"])]
        print("received: ", entry["y_data"])
    print("")
    return data

#initialization
#feel free to try different acquisition functions, e.g. optional_acq_func, "covariance", "shannon_ig"
#note how costs are defined in for the autonomous experimenter
my_ae = AutonomousExperimenterGP(np.array([[0,10],[0,10]]),
                                 np.ones((3)), np.array([[0.001,100.],[0.001,100.],[0.001,100.]]),
                                 init_dataset_size= 20, instrument_function = instrument,
                                 acquisition_function = optional_acq_func, 
                                 cost_function = optional_cost_function, 
                                 cost_update_function = optional_cost_update_function,
                                 cost_function_parameters={"offset": 5.0,"slope":10.0},
                                 kernel_function = None, store_inv = True,
                                 prior_mean_function = optional_mean_func,
                                 communicate_full_dataset = False, ram_economy = True)#, info = False, prior_mean_func = optional_mean_func)


print("length of the dataset: ",len(my_ae.x_data))


#my_ae.train_async()                 #train asynchronously
my_ae.train(method = "global")       #or not, or both, choose between "global","local" and "hgdl"

Suggested by gpCAM: 
suggested: [8.21167511 6.50448298]
received:  -0.8678725453266757
suggested: [1.45353157 8.13994477]
received:  0.9152284912421352
suggested: [3.0971043  4.66027056]
received:  -0.6347118563370081
suggested: [8.24905231 2.97355126]
received:  0.6100692722101375
suggested: [4.68416047 9.38269055]
received:  -0.8734180807175406
suggested: [8.52700417 2.16152341]
received:  0.5875881844948109
suggested: [3.83976022 4.28704906]
received:  -0.5037774266585683
suggested: [7.59044561 4.77379081]
received:  0.4421132886524308
suggested: [5.20065424 6.46806603]
received:  0.902361901079506
suggested: [3.46753072 1.60575398]
received:  -0.6285533739036385
suggested: [6.2025569 1.9717227]
received:  0.22332552220359608
suggested: [3.71985449 9.4739396 ]
received:  -0.684034493741265
suggested: [3.36723518 0.7263417 ]
received:  -0.2984716713417215
suggested: [4.84035908 6.43390549]
received:  0.980586263437355
suggested: [5.21378265 6.82655185]
received:  0.7412553206820042
s

In [7]:
#update hyperparameters in case they are optimized asynchronously
my_ae.update_hps()
print(my_ae.gp_optimizer.hyperparameters)

[2.29554516 5.84101702 5.09845941]


In [8]:
#training and client can be killed if desired and in case they are optimized asynchronously
my_ae.kill_training()

## Let's see what our initial model looks like

In [9]:
f = my_ae.gp_optimizer.posterior_mean(x_pred)["f(x)"]
f_re = f.reshape(100,100)

plot(x,y,f_re, data = np.column_stack([my_ae.x_data,my_ae.y_data]))

## Let's run the autonomus loop to 100 points

In [10]:
#run the autonomous loop
my_ae.go(N = 100, 
            retrain_async_at=[30,40,50,60,70,80,90],
            retrain_globally_at = [20,22,24,26,28,30,40,50,60,70],
            retrain_locally_at = [21,22,56,78],
            acq_func_opt_setting = lambda number: "global" if number % 2 == 0 else "local",
            update_cost_func_at = (50,),
            training_opt_max_iter = 20,
            training_opt_pop_size = 10,
            training_opt_tol      = 1e-6,
            acq_func_opt_max_iter = 20,
            acq_func_opt_pop_size = 20,
            acq_func_opt_tol      = 1e-6,
            number_of_suggested_measurements = 1,
            acq_func_opt_tol_adjust = 0.1)

Suggested by gpCAM: 
suggested: [3.06826564e-03 9.74121693e+00]
received:  -0.3111847775135406

Suggested by gpCAM: 
suggested: [2.8672337  3.27287697]
received:  -0.9354696526773818

Suggested by gpCAM: 
suggested: [0.30945821 0.12802659]
received:  0.3286707548796835

Suggested by gpCAM: 
suggested: [0.29144193 3.75754671]
received:  -0.5869119435262886

Suggested by gpCAM: 
suggested: [0.11297561 6.97634303]
received:  0.639672745342733

Suggested by gpCAM: 
suggested: [9.68119139 8.58531772]
received:  0.3646207468015457

Suggested by gpCAM: 
suggested: [2.99389617 7.01503989]
received:  0.9743953487198904

Suggested by gpCAM: 
suggested: [2.97510844 7.01503913]
received:  0.9727151043112818

Suggested by gpCAM: 
suggested: [9.84703576 3.04418234]
received:  -0.7720575039503464

Suggested by gpCAM: 
suggested: [0.14312303 7.8216414 ]
received:  0.999518580707008

Suggested by gpCAM: 
suggested: [9.80790496 9.91381066]
received:  0.9816994677355744

Suggested by gpCAM: 
suggested: [

Suggested by gpCAM: 
suggested: [1.13041114 1.2576894 ]
received:  0.9927795881465064

Suggested by gpCAM: 
suggested: [4.5192757 5.8756897]
received:  0.9041894947906844

Suggested by gpCAM: 
suggested: [6.00869135 4.2017845 ]
received:  0.8668716260923229

Suggested by gpCAM: 
suggested: [6.00869671 3.59962902]
received:  0.6603052159253704

Suggested by gpCAM: 
suggested: [0.53286397 1.64037067]
received:  0.9881726381536178

Suggested by gpCAM: 
suggested: [2.77903205 4.36260129]
received:  -0.8959794715470345

Suggested by gpCAM: 
suggested: [7.87092831 1.2796806 ]
received:  0.9927732245166284

Suggested by gpCAM: 
suggested: [4.62011326 5.54340827]
received:  0.8034713579728339

Suggested by gpCAM: 
suggested: [1.7457974  0.25120306]
received:  0.9814368253247775

Suggested by gpCAM: 
suggested: [3.20191304 7.90787487]
received:  0.7791219457252169

Suggested by gpCAM: 
suggested: [0.66444172 1.17364793]
received:  0.9754329713988941

Suggested by gpCAM: 
suggested: [0.80354733 






## Now let's plot the posterior mean after the experiment has concluded

In [11]:
res = my_ae.gp_optimizer.posterior_mean(x_pred)
f = res["f(x)"]
f = f.reshape(100,100)

plot(x,y,f, data = np.column_stack([my_ae.x_data,my_ae.y_data]))

## Running a Multi-Task GP Autonomous Data Acquisition
This example uses 21 (!) dim robot data and 7 tasks, which you can all use or pick a subset of them

In [12]:
##prepare some data
import numpy as np
from scipy.interpolate import griddata
data = np.load("./data/sarcos.npy")
print(data.shape)
x = data[:,0:21]
y = data[:,21:23]

(4449, 28)


In [13]:
from gpcam import AutonomousExperimenterFvGP

def instrument(data, instrument_dict = {}):
    for entry in data:
        print("Suggested by gpCAM: ", entry["x_data"])
        entry["y_data"] = griddata(x,y,entry["x_data"],method = "nearest", fill_value = 0)[0]
        entry["output positions"] = np.array([[0],[1]])
        print("received: ", entry["y_data"])
    print("")
    return data

def acq_func(x,obj):
    #multi-tast autonomous experiments should make use of a user-defined acquisition function to
    #make full use of the surrogate and the uncertainty in all tasks.
    a = 3.0 #3.0 for ~95 percent confidence interval
    x = np.block([[x,np.zeros((len(x))).reshape(-1,1)],[x,np.ones((len(x))).reshape(-1,1)]]) #for task 0 and 1
    mean = obj.posterior_mean(x)["f(x)"]
    cov = obj.posterior_covariance(x)["v(x)"]
    #it takes a little bit of wiggling to get the tasks seperated and then merged again...
    task0index = np.where(x[:,21] == 0.)[0]
    task1index = np.where(x[:,21] == 1.)[0]
    mean_task0 = mean[task0index]
    mean_task1 = mean[task1index]
    cov_task0 = cov[task0index]
    cov_task1 = cov[task1index]
    mean = np.column_stack([mean_task0,mean_task1])
    cov  = np.column_stack([cov_task0 ,cov_task1 ])
    #and now we are interested in the l2 norm of the mean and variance at each input location.
    return np.linalg.norm(mean, axis = 1) + a * np.linalg.norm(cov,axis = 1)


input_s = np.array([np.array([np.min(x[:,i]),np.max(x[:,i])]) for i in range(len(x[0]))])
print("index set (input space) bounds:")
print(input_s)
print("hps bounds:")
hps_bounds = np.empty((23,2))
hps_bounds[:,0] = 0.0001
hps_bounds[:,1] = 100.0
hps_bounds[0] = np.array([0.0001, 10000])
print(hps_bounds)
print("shape of y: ")
print(y.shape)

my_fvae = AutonomousExperimenterFvGP(input_s,2,1,
                                     init_dataset_size= 10, instrument_function = instrument, \
                                     acquisition_function=acq_func)


my_fvae.train()
my_fvae.go(N = 50, retrain_async_at=(22,), retrain_globally_at=(50,90,120), retrain_locally_at=(25,))

index set (input space) bounds:
[[ -0.842481   0.661032]
 [ -0.939933  -0.085018]
 [ -0.46773    0.359348]
 [  0.797788   2.239407]
 [ -0.242241   1.278097]
 [ -0.919895   0.369078]
 [ -0.296364   0.686928]
 [ -4.771399   4.488624]
 [ -1.634053   2.289369]
 [ -2.884804   2.558282]
 [ -4.196409   3.734968]
 [ -3.067483   2.380553]
 [ -2.433971   1.978575]
 [ -3.180643   2.568279]
 [-48.072386  48.872604]
 [-25.585054  25.225171]
 [-24.697862  26.106756]
 [-36.19139   71.176937]
 [-38.485967  35.804308]
 [-22.103174  17.84188 ]
 [-36.502723  30.806254]]
hps bounds:
[[1.e-04 1.e+04]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]]
shape of y: 
(4449, 2)
Suggested by gp

Suggested by gpCAM:  [ -0.09268668  -0.18070223   0.23213901   1.5618587    0.89167638
  -0.62408059   0.49954217  -2.09435544  -0.85095451  -2.46044996
  -2.42187199   1.72490755  -1.23097857  -2.40591029   0.50658315
  -5.31232069   8.05873965 -28.54355798  27.84155083 -13.08298352
   4.7210061 ]
received:  [  3.670004 -27.864849]

Suggested by gpCAM:  [ -0.58701376  -0.45494867  -0.36407151   1.74890682   1.09359549
  -0.42055012   0.31438172   1.30899847   0.20589426   1.90967622
   3.52357379   0.7232675    1.09809934   0.77719783 -26.36780299
  -7.9563702   -6.04197965  68.9859534  -31.57099549 -20.87729515
  15.8022618 ]
received:  [ -0.67963  -31.398928]

Suggested by gpCAM:  [ -0.30740362  -0.09255303  -0.35827918   1.26444717   0.69091973
  -0.63305223   0.37379263  -1.36540025  -1.23343951   2.02316359
  -0.24956923  -2.6710802   -1.35975473   0.59476953 -28.43970524
 -21.74640753   1.33912953  -5.68891936   7.66141234   9.02549332
  -1.23904127]
received:  [-34.933006 -39.2

Suggested by gpCAM:  [  0.30002403  -0.31731936   0.32324599   1.46627912   0.78245264
  -0.88006341   0.1819452   -4.66876953   0.99434623  -2.2102361
  -0.72685305  -2.58541962   0.87294553  -2.1250897  -35.26613832
 -20.27184618   0.28148989   7.32938161 -10.41219685 -12.09806653
   6.03767691]
received:  [-34.933006 -39.282639]

Suggested by gpCAM:  [-5.74668118e-01 -9.20748442e-01  3.41176969e-01  1.21415578e+00
  1.20761447e+00 -6.44187488e-01  5.30261991e-01 -2.75212358e+00
 -3.05860219e-02 -1.01754958e+00 -3.22709248e+00  2.09698104e+00
 -5.60272852e-01  6.67992444e-01 -4.11034685e+01 -1.41730025e+00
 -1.56015851e+01 -1.72233946e+00  2.10144723e+01  1.17825105e+01
 -2.01291982e+01]
received:  [-65.788231  -8.835196]

Suggested by gpCAM:  [ -0.68781715  -0.70872134   0.14202993   2.00003481  -0.14189469
  -0.2022066    0.13370038  -1.55631436   0.30885276   1.49375785
  -1.26812687   0.31146849   0.98298188   1.64100139  23.64519464
  -2.43478166  -6.40163902  16.15668958 -16.00

2023-11-02 17:30:11,098 - distributed.nanny - WARNING - Worker process still alive after 3.199999389648438 seconds, killing


## Plotting the 0th task in a 2d slice

In [14]:
x_pred = np.zeros((10000,22))
x = np.linspace(input_s[0,0],input_s[0,1],100)
y = np.linspace(input_s[1,0],input_s[1,1],100)
x,y = np.meshgrid(x,y)
counter = 0
for i in  range(100):
    for j in range(100):
        x_pred[counter] = np.zeros((22))
        x_pred[counter,[0,1,-1]] = np.array([x[i,j],y[i,j],0.])
        counter += 1
res = my_fvae.gp_optimizer.posterior_mean(x_pred)
f = res["f(x)"]
f = f.reshape(100,100)

plot(x,y,f)